In [1]:
import torch
from torch.optim import AdamW, Adam
from torch.utils.data import DataLoader, Dataset
import os
from torch.nn.functional import one_hot

import torch
import torch.nn as nn

import joblib
import numpy as np
import math

# Data preparation

In [2]:
entokened = joblib.load("/kaggle/input/tokenized-test3/tokenized_test3.pkl")
print(len(entokened))

512


In [18]:
import random as rd
def load_and_tokenized(file):
    return file

class MyDataset(Dataset):
    def __init__(self):
        self.files = entokened

    def __len__(self):
        return len(self.files)

    def __getitem__(self, index):
        return torch.tensor(self.files[index])[:2000]

def my_collate_fn(batch):
    sequences = batch

    max_len = max([seq.size(0) for seq in sequences])

    padded_sequences = []
    padding_value = 2700

    for seq in sequences:
        padding_needed = max_len - seq.size(0)
        padded_seq = torch.nn.functional.pad(seq, (0, padding_needed), value=padding_value)
        padded_sequences.append(padded_seq)

    batch_tensor = torch.stack(padded_sequences, dim=0)
    return batch_tensor


In [19]:
dataset = MyDataset()
dataloader = DataLoader(dataset, batch_size=32, collate_fn=my_collate_fn)

In [20]:
print(dataset[10].shape)

torch.Size([1322])


# Model

In [21]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'

device

'cuda'

In [11]:
import torch
import torch.nn as nn
import math

class SingleLayerTransformer(nn.Module):
    def __init__(self, vocab_size, d_model=256, num_heads=8, dim_feedforward=3024, max_seq_len=2000, dropout=0.1):
        super().__init__()
        self.token_embed = nn.Embedding(vocab_size, d_model)
        pe = torch.zeros(max_seq_len, d_model)
        position = torch.arange(0, max_seq_len).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2) * -(math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)
        self.register_buffer('pos_embed', pe.unsqueeze(0))  # shape (1, max_seq_len, d_model)

        self.attention = nn.MultiheadAttention(d_model, num_heads, dropout=dropout, batch_first=True)
        self.norm1 = nn.LayerNorm(d_model)
        self.dropout1 = nn.Dropout(dropout)

        self.ffn = nn.Sequential(
            nn.Linear(d_model, dim_feedforward),
            nn.ReLU(),
            nn.Dropout(dropout),
            nn.Linear(dim_feedforward, d_model),
        )
        self.norm2 = nn.LayerNorm(d_model)
        self.dropout2 = nn.Dropout(dropout)

    def forward(self, input_ids, attention_mask=None, labels=None):
        x = self.token_embed(input_ids)                   # (batch, seq_len, d_model)
        seq_len = x.size(1)
        pos = self.pos_embed[:, :seq_len, :]
        x = x + pos

        device = x.device
        causal_mask = torch.triu(torch.full((seq_len, seq_len), float('-inf'), device=device), diagonal=1)

        key_padding_mask = None
        if attention_mask is not None:
            key_padding_mask = attention_mask == 0 

        attn_output, attn_weights = self.attention(
            query=x,
            key=x,
            value=x,
            attn_mask=causal_mask,
            key_padding_mask=key_padding_mask,
            need_weights=True,
        )  # attn_output: (batch, seq_len, d_model)
        x = x + self.dropout1(attn_output)
        x = self.norm1(x)

        ffn_output = self.ffn(x)
        x = x + self.dropout2(ffn_output)
        x = self.norm2(x)

        logits = self.token_embed.weight @ x.transpose(1,2)
        logits = logits.transpose(1,2)  # (batch, seq_len, vocab_size)
        
        loss = None
        if labels is not None:
            shift_logits = logits[..., :-1, :].contiguous()
            shift_labels = labels[..., 1:].contiguous()
            loss_fct = nn.CrossEntropyLoss(ignore_index=2700) 
            loss = loss_fct(shift_logits.view(-1, shift_logits.size(-1)), shift_labels.view(-1))

        return logits, loss


        # return x, attn_weights

In [22]:
vocab_size = 2700

model = SingleLayerTransformer(vocab_size=vocab_size)
model = model.to(device)
if torch.cuda.device_count() > 1:
    print("Let's use", torch.cuda.device_count(), "GPUs!")
    model = nn.DataParallel(model).cuda()

optimizer = Adam(model.parameters(), lr=0.0001)
loss_fn = torch.nn.CrossEntropyLoss(ignore_index=2700)
epochs = 12
total_params = sum(p.numel() for p in model.parameters())
f"{total_params:,}"


Let's use 2 GPUs!


'2,506,960'

In [49]:
import gc
gc.collect()
torch.cuda.empty_cache()

del pred
del losses
del model
del optimizer
del batch


NameError: name 'pred' is not defined

In [24]:
from tqdm import tqdm
model.train()
with torch.autograd.set_detect_anomaly(True):
    for epoch in range(1):
        total_loss = 0.0
        for batch in (tqdm(dataloader)):
            input_ids = batch.to(device)
            attention_mask = torch.where(batch == 2700, 0, 1).to(device)
            labels = batch.to(device) 
            optimizer.zero_grad()
            _, loss = model(input_ids, attention_mask=attention_mask, labels=labels)
            print(loss)
            break
            loss.backward()
            optimizer.step()
    
            total_loss += loss.item()
        print(total_loss / len(train_loader))


  0%|          | 0/16 [00:01<?, ?it/s]


RuntimeError: Caught RuntimeError in replica 0 on device 0.
Original Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/nn/parallel/parallel_apply.py", line 96, in _worker
    output = module(*input, **kwargs)
             ^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py", line 1736, in _wrapped_call_impl
    return self._call_impl(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py", line 1747, in _call_impl
    return forward_call(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/tmp/ipykernel_31/3299460130.py", line 33, in forward
    x = x + pos
        ~~^~~~~
RuntimeError: The size of tensor a (2000) must match the size of tensor b (512) at non-singleton dimension 1


../aten/src/ATen/native/cuda/Indexing.cu:1308: indexSelectLargeIndex: block: [58,0,0], thread: [64,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1308: indexSelectLargeIndex: block: [58,0,0], thread: [65,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1308: indexSelectLargeIndex: block: [58,0,0], thread: [66,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1308: indexSelectLargeIndex: block: [58,0,0], thread: [67,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1308: indexSelectLargeIndex: block: [58,0,0], thread: [68,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1308: indexSelectLargeIndex: block: [58,0,0], thread: [69,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1308: indexSelectLargeIndex: block: [58,0,0], t

In [51]:
for epoch in range(epochs):
    losses = []
    for i, batch in enumerate(dataloader):
        optimizer.zero_grad()
        batch = batch.to(device)
        preds = model(batch[:, :-1])

        batch_size, sequence_length, vocab_size = preds.shape

        loss = loss_fn(preds.view(-1, vocab_size), batch[:, 1:].contiguous().view(-1))

        loss.backward()
        optimizer.step()

        losses.append(loss.item())
        if i % 100 == 0:
             print(f"epoch: {epoch}, loss: {loss.item():.4f}")
    print(f"Epoch {epoch+1} Mean Loss: {np.mean(losses):.4f}")

epoch: 0, loss: 8.0912


OutOfMemoryError: Caught OutOfMemoryError in replica 0 on device 0.
Original Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/nn/parallel/parallel_apply.py", line 96, in _worker
    output = module(*input, **kwargs)
             ^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py", line 1736, in _wrapped_call_impl
    return self._call_impl(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py", line 1747, in _call_impl
    return forward_call(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/tmp/ipykernel_31/867588751.py", line 67, in forward
    x = block(x, key_padding_mask=padding_mask)
       ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py", line 1736, in _wrapped_call_impl
    return self._call_impl(*args, **kwargs)
           ^^^

In [19]:
example = dataset[13]


In [22]:
example = torch.tensor([2691])

In [ ]:
for _ in range(60):
    with torch.no_grad():
        pred = model(example.unsqueeze(0).to(device))[0, -1, :]
        pred = torch.argmax(pred, dim=-1).cpu()
    
    example = torch.cat((example, pred.unsqueeze(0)))
example

In [23]:
from torch.distributions import Categorical

example = example.unsqueeze(0)
for _ in range(40):
    with torch.no_grad():
        logits = model(example.to(device))
        probabilities = torch.nn.functional.softmax(logits, dim=-1)
        batch_size, sequence_length, vocab_size = logits.shape
        probabilities_flat = probabilities.view(-1, vocab_size)
        dist = Categorical(probabilities_flat)
        sampled_indices_flat = dist.sample()
        pred = sampled_indices_flat.view(batch_size, sequence_length)[:, -1:]
        pred = pred.cpu()
        
    #print(example.shape, pred.shape)
    example = torch.cat((example, pred), dim=1)
example.cpu().numpy().tolist()[-60:]

[[2691,
  2662,
  2178,
  1762,
  1987,
  2049,
  2213,
  2249,
  2186,
  2369,
  1091,
  1890,
  2051,
  1925,
  2214,
  2153,
  615,
  1736,
  1650,
  1554,
  2081,
  1957,
  1512,
  1480,
  1544,
  1514,
  1708,
  2671,
  1468,
  527,
  932,
  1892,
  1796,
  2019,
  1923,
  1573,
  1034,
  1579,
  1547,
  1675,
  1484]]